In [48]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [49]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [50]:
# Convolutional neural network (two convolutional layers)
class LSTM_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(LSTM_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.rnn = nn.LSTM(64,256,dropout=0.25)
        self.fc1 = nn.Linear(256, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(256, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.rnn(x)
        #b,64,256
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,256 * b,64,1 = b,64,256
        x = torch.sum(x,dim=1)
        #b,64,256 -> b,,256
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [51]:
test = LSTM_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

torch.Size([10, 4])

In [52]:
writer = SummaryWriter()

In [53]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [54]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [55]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [56]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [57]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [58]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [60]:
model = LSTM_AT(num_classes).to(device)

In [61]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [62]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 26.5625%, Training Loss: 1.6274%
Epoch [1/300], Step [2/225], Training Accuracy: 24.2188%, Training Loss: 1.5561%
Epoch [1/300], Step [3/225], Training Accuracy: 25.0000%, Training Loss: 1.5173%
Epoch [1/300], Step [4/225], Training Accuracy: 23.0469%, Training Loss: 1.5154%
Epoch [1/300], Step [5/225], Training Accuracy: 23.4375%, Training Loss: 1.4963%
Epoch [1/300], Step [6/225], Training Accuracy: 22.9167%, Training Loss: 1.4845%
Epoch [1/300], Step [7/225], Training Accuracy: 23.8839%, Training Loss: 1.4833%
Epoch [1/300], Step [8/225], Training Accuracy: 23.8281%, Training Loss: 1.4770%
Epoch [1/300], Step [9/225], Training Accuracy: 24.4792%, Training Loss: 1.4833%
Epoch [1/300], Step [10/225], Training Accuracy: 23.9062%, Training Loss: 1.4908%
Epoch [1/300], Step [11/225], Training Accuracy: 24.2898%, Training Loss: 1.4940%
Epoch [1/300], Step [12/225], Training Accuracy: 24.4792%, Training Loss: 1.4926%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [116/225], Training Accuracy: 28.0442%, Training Loss: 1.4112%
Epoch [1/300], Step [117/225], Training Accuracy: 28.0716%, Training Loss: 1.4112%
Epoch [1/300], Step [118/225], Training Accuracy: 28.0985%, Training Loss: 1.4112%
Epoch [1/300], Step [119/225], Training Accuracy: 28.0200%, Training Loss: 1.4112%
Epoch [1/300], Step [120/225], Training Accuracy: 28.0208%, Training Loss: 1.4111%
Epoch [1/300], Step [121/225], Training Accuracy: 27.9700%, Training Loss: 1.4109%
Epoch [1/300], Step [122/225], Training Accuracy: 28.0610%, Training Loss: 1.4102%
Epoch [1/300], Step [123/225], Training Accuracy: 28.1123%, Training Loss: 1.4098%
Epoch [1/300], Step [124/225], Training Accuracy: 28.0116%, Training Loss: 1.4096%
Epoch [1/300], Step [125/225], Training Accuracy: 27.9375%, Training Loss: 1.4101%
Epoch [1/300], Step [126/225], Training Accuracy: 27.9018%, Training Loss: 1.4101%
Epoch [1/300], Step [127/225], Training Accuracy: 27.8912%, Training Loss: 1.4098%
Epoc

Epoch [1/300], Step [215/225], Training Accuracy: 29.5785%, Training Loss: 1.3842%
Epoch [1/300], Step [216/225], Training Accuracy: 29.5573%, Training Loss: 1.3842%
Epoch [1/300], Step [217/225], Training Accuracy: 29.5723%, Training Loss: 1.3839%
Epoch [1/300], Step [218/225], Training Accuracy: 29.5657%, Training Loss: 1.3840%
Epoch [1/300], Step [219/225], Training Accuracy: 29.6304%, Training Loss: 1.3834%
Epoch [1/300], Step [220/225], Training Accuracy: 29.7017%, Training Loss: 1.3827%
Epoch [1/300], Step [221/225], Training Accuracy: 29.6875%, Training Loss: 1.3829%
Epoch [1/300], Step [222/225], Training Accuracy: 29.7227%, Training Loss: 1.3823%
Epoch [1/300], Step [223/225], Training Accuracy: 29.7295%, Training Loss: 1.3822%
Epoch [1/300], Step [224/225], Training Accuracy: 29.7712%, Training Loss: 1.3817%
Epoch [1/300], Step [225/225], Training Accuracy: 29.7457%, Training Loss: 1.3818%
Epoch [2/300], Step [1/225], Training Accuracy: 37.5000%, Training Loss: 1.2858%
Epoch 

Epoch [2/300], Step [92/225], Training Accuracy: 34.8675%, Training Loss: 1.3135%
Epoch [2/300], Step [93/225], Training Accuracy: 34.9126%, Training Loss: 1.3131%
Epoch [2/300], Step [94/225], Training Accuracy: 34.9734%, Training Loss: 1.3133%
Epoch [2/300], Step [95/225], Training Accuracy: 34.8684%, Training Loss: 1.3144%
Epoch [2/300], Step [96/225], Training Accuracy: 34.8633%, Training Loss: 1.3138%
Epoch [2/300], Step [97/225], Training Accuracy: 34.8744%, Training Loss: 1.3140%
Epoch [2/300], Step [98/225], Training Accuracy: 34.8055%, Training Loss: 1.3146%
Epoch [2/300], Step [99/225], Training Accuracy: 34.7854%, Training Loss: 1.3145%
Epoch [2/300], Step [100/225], Training Accuracy: 34.7812%, Training Loss: 1.3141%
Epoch [2/300], Step [101/225], Training Accuracy: 34.7772%, Training Loss: 1.3135%
Epoch [2/300], Step [102/225], Training Accuracy: 34.7886%, Training Loss: 1.3133%
Epoch [2/300], Step [103/225], Training Accuracy: 34.7391%, Training Loss: 1.3135%
Epoch [2/300

Epoch [2/300], Step [204/225], Training Accuracy: 34.7656%, Training Loss: 1.3069%
Epoch [2/300], Step [205/225], Training Accuracy: 34.7561%, Training Loss: 1.3068%
Epoch [2/300], Step [206/225], Training Accuracy: 34.7618%, Training Loss: 1.3068%
Epoch [2/300], Step [207/225], Training Accuracy: 34.7600%, Training Loss: 1.3073%
Epoch [2/300], Step [208/225], Training Accuracy: 34.8182%, Training Loss: 1.3068%
Epoch [2/300], Step [209/225], Training Accuracy: 34.8161%, Training Loss: 1.3068%
Epoch [2/300], Step [210/225], Training Accuracy: 34.8810%, Training Loss: 1.3063%
Epoch [2/300], Step [211/225], Training Accuracy: 34.8711%, Training Loss: 1.3061%
Epoch [2/300], Step [212/225], Training Accuracy: 34.8688%, Training Loss: 1.3058%
Epoch [2/300], Step [213/225], Training Accuracy: 34.8592%, Training Loss: 1.3060%
Epoch [2/300], Step [214/225], Training Accuracy: 34.9007%, Training Loss: 1.3055%
Epoch [2/300], Step [215/225], Training Accuracy: 34.8837%, Training Loss: 1.3055%
Epoc

...

Epoch [298/300], Step [168/225], Training Accuracy: 99.6838%, Training Loss: 0.0180%
Epoch [298/300], Step [169/225], Training Accuracy: 99.6857%, Training Loss: 0.0180%
Epoch [298/300], Step [170/225], Training Accuracy: 99.6875%, Training Loss: 0.0180%
Epoch [298/300], Step [171/225], Training Accuracy: 99.6893%, Training Loss: 0.0179%
Epoch [298/300], Step [172/225], Training Accuracy: 99.6820%, Training Loss: 0.0181%
Epoch [298/300], Step [173/225], Training Accuracy: 99.6839%, Training Loss: 0.0181%
Epoch [298/300], Step [174/225], Training Accuracy: 99.6857%, Training Loss: 0.0180%
Epoch [298/300], Step [175/225], Training Accuracy: 99.6875%, Training Loss: 0.0180%
Epoch [298/300], Step [176/225], Training Accuracy: 99.6893%, Training Loss: 0.0179%
Epoch [298/300], Step [177/225], Training Accuracy: 99.6822%, Training Loss: 0.0180%
Epoch [298/300], Step [178/225], Training Accuracy: 99.6840%, Training Loss: 0.0179%
Epoch [298/300], Step [179/225], Training Accuracy: 99.6858%, Tra

Epoch [299/300], Step [55/225], Training Accuracy: 99.6591%, Training Loss: 0.0180%
Epoch [299/300], Step [56/225], Training Accuracy: 99.6652%, Training Loss: 0.0178%
Epoch [299/300], Step [57/225], Training Accuracy: 99.6711%, Training Loss: 0.0177%
Epoch [299/300], Step [58/225], Training Accuracy: 99.6767%, Training Loss: 0.0176%
Epoch [299/300], Step [59/225], Training Accuracy: 99.6822%, Training Loss: 0.0174%
Epoch [299/300], Step [60/225], Training Accuracy: 99.6875%, Training Loss: 0.0174%
Epoch [299/300], Step [61/225], Training Accuracy: 99.6926%, Training Loss: 0.0173%
Epoch [299/300], Step [62/225], Training Accuracy: 99.6976%, Training Loss: 0.0172%
Epoch [299/300], Step [63/225], Training Accuracy: 99.7024%, Training Loss: 0.0170%
Epoch [299/300], Step [64/225], Training Accuracy: 99.7070%, Training Loss: 0.0169%
Epoch [299/300], Step [65/225], Training Accuracy: 99.6875%, Training Loss: 0.0171%
Epoch [299/300], Step [66/225], Training Accuracy: 99.6686%, Training Loss: 

Epoch [299/300], Step [166/225], Training Accuracy: 99.5764%, Training Loss: 0.0194%
Epoch [299/300], Step [167/225], Training Accuracy: 99.5790%, Training Loss: 0.0195%
Epoch [299/300], Step [168/225], Training Accuracy: 99.5815%, Training Loss: 0.0195%
Epoch [299/300], Step [169/225], Training Accuracy: 99.5747%, Training Loss: 0.0195%
Epoch [299/300], Step [170/225], Training Accuracy: 99.5772%, Training Loss: 0.0195%
Epoch [299/300], Step [171/225], Training Accuracy: 99.5797%, Training Loss: 0.0195%
Epoch [299/300], Step [172/225], Training Accuracy: 99.5730%, Training Loss: 0.0197%
Epoch [299/300], Step [173/225], Training Accuracy: 99.5755%, Training Loss: 0.0196%
Epoch [299/300], Step [174/225], Training Accuracy: 99.5779%, Training Loss: 0.0197%
Epoch [299/300], Step [175/225], Training Accuracy: 99.5714%, Training Loss: 0.0197%
Epoch [299/300], Step [176/225], Training Accuracy: 99.5739%, Training Loss: 0.0196%
Epoch [299/300], Step [177/225], Training Accuracy: 99.5763%, Tra

Epoch [300/300], Step [49/225], Training Accuracy: 99.7130%, Training Loss: 0.0176%
Epoch [300/300], Step [50/225], Training Accuracy: 99.7188%, Training Loss: 0.0175%
Epoch [300/300], Step [51/225], Training Accuracy: 99.6936%, Training Loss: 0.0177%
Epoch [300/300], Step [52/225], Training Accuracy: 99.6995%, Training Loss: 0.0178%
Epoch [300/300], Step [53/225], Training Accuracy: 99.7052%, Training Loss: 0.0179%
Epoch [300/300], Step [54/225], Training Accuracy: 99.6817%, Training Loss: 0.0182%
Epoch [300/300], Step [55/225], Training Accuracy: 99.6591%, Training Loss: 0.0184%
Epoch [300/300], Step [56/225], Training Accuracy: 99.6652%, Training Loss: 0.0184%
Epoch [300/300], Step [57/225], Training Accuracy: 99.6436%, Training Loss: 0.0186%
Epoch [300/300], Step [58/225], Training Accuracy: 99.6498%, Training Loss: 0.0186%
Epoch [300/300], Step [59/225], Training Accuracy: 99.6557%, Training Loss: 0.0187%
Epoch [300/300], Step [60/225], Training Accuracy: 99.6615%, Training Loss: 

Epoch [300/300], Step [156/225], Training Accuracy: 99.6895%, Training Loss: 0.0190%
Epoch [300/300], Step [157/225], Training Accuracy: 99.6915%, Training Loss: 0.0190%
Epoch [300/300], Step [158/225], Training Accuracy: 99.6934%, Training Loss: 0.0189%
Epoch [300/300], Step [159/225], Training Accuracy: 99.6954%, Training Loss: 0.0189%
Epoch [300/300], Step [160/225], Training Accuracy: 99.6973%, Training Loss: 0.0189%
Epoch [300/300], Step [161/225], Training Accuracy: 99.6894%, Training Loss: 0.0190%
Epoch [300/300], Step [162/225], Training Accuracy: 99.6817%, Training Loss: 0.0190%
Epoch [300/300], Step [163/225], Training Accuracy: 99.6837%, Training Loss: 0.0189%
Epoch [300/300], Step [164/225], Training Accuracy: 99.6856%, Training Loss: 0.0188%
Epoch [300/300], Step [165/225], Training Accuracy: 99.6875%, Training Loss: 0.0188%
Epoch [300/300], Step [166/225], Training Accuracy: 99.6894%, Training Loss: 0.0188%
Epoch [300/300], Step [167/225], Training Accuracy: 99.6912%, Tra

In [2]:
from playsound import playsound
playsound(u"sound.mp3")

In [64]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 41.662034463590885 %
